In [1]:
#We are creating a mount while will allow us to access our dataset through our Amazon S3 account

import urllib
ACCESS_KEY = "******"
SECRET_KEY = "******"
ENCODED_SECRET_KEY = SECRET_KEY.replace("/", "%2F")    
AWS_BUCKET_NAME = "*****"
MOUNT_NAME = "******"

#Remove the below line's "#" if this is the first time running this Notebook, after that you will need to comment it out (Use a #), as there will already be a mount created
dbutils.fs.mount("s3a://%s:%s@%s" % (ACCESS_KEY, ENCODED_SECRET_KEY, AWS_BUCKET_NAME), "/mnt/%s" % MOUNT_NAME)

display(dbutils.fs.ls("/mnt/%s" % MOUNT_NAME))

path name size dbfs:/mnt/inst767-mount/business.json business.json 138279749 dbfs:/mnt/inst767-mount/checkin.json checkin.json 408807658 dbfs:/mnt/inst767-mount/review.json review.json 5347475638 dbfs:/mnt/inst767-mount/tip.json tip.json 244535478 dbfs:/mnt/inst767-mount/user.json user.json 2485747393

#### Read the User dataset from JSON format and storing it as Pyspark dataframe

In [3]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, BooleanType, FloatType, ArrayType, TimestampType

In [4]:
#Reading the Amazon S3 User dataset from JSON format and storing it as Pyspark dataframe
user_schema = StructType([StructField('average_stars', FloatType(), True),
                         StructField('compliment_cool', IntegerType(), True),
                         StructField('compliment_funny', IntegerType(), True),
                         StructField('compliment_hot', IntegerType(), True),
                         StructField('compliment_list', IntegerType(), True),
                         StructField('compliment_more', IntegerType(), True),
                         StructField('compliment_note', IntegerType(), True),
                         StructField('compliment_photos', IntegerType(), True),
                         StructField('compliment_plain', IntegerType(), True),
                         StructField('compliment_profile', IntegerType(), True),
                         StructField('compliment_writer', IntegerType(), True),
                         StructField('cool', IntegerType(), True),
                         StructField('elite', StringType(), True),
                         StructField('fans', IntegerType(), True),
                         StructField('friends', StringType(), True),
                         StructField('funny', IntegerType(), True),
                         StructField('name', StringType(), True),
                         StructField('review_count', IntegerType(), True),
                         StructField('useful', IntegerType(), True),
                         StructField('user_id', StringType(), True),
                         StructField('yelping_since', TimestampType(), True)])

Users_df = spark.read.json("dbfs:/mnt/inst767-mount/user.json", schema = user_schema)

Users_df = Users_df.withColumnRenamed('review_count', 'user_review_count')

#Double check the schema of the dataframe represnting the Users dataset
Users_df.printSchema()

#Keeping only the columns that we want to use for our analysis
Users_refined_df = Users_df.select([c for c in Users_df.columns if c in ['user_id', 'average_stars', 'fans', 'user_review_count']])

display(Users_refined_df)

average_stars fans user_review_count user_id 4.03 5 95 l6BmjZMeQD3rDxWUbiAiow 3.63 4 33 4XChL029mKr5hydo79Ljxg 3.71 0 16 bc8C_eETBWL0olvFSJJd0w 4.85 5 17 dD0gZpBctWGdWo9WlGuhlA 4.08 39 361 MM4RJAeH6yuaN8oZDSt0RA 4.2 186 214 0rK89TS8xqy1wI4nYI1wfw 4.39 696 1122 TEtzbpgA2BFBrC0y0sCbfw 4.33 0 6 KGuqerdeNhxzXZEyBaqqSw 4.21 57 859 T0gWkTHWRChVUe_Dn1F8nw 4.53 15 124 NQffx45eJaeqhFcMadKUQA 3.6 9 47 gvXtMj3XuPr0xHjgmlmtng 3.48 3 77 _DaFdmq0gtXf1spn1qC_1Q 3.5 2 11 FTWKZZeLb_0ZJRXQg8WADw 3.95 0 22 US0VOSMFs9U0Nkl5Vx1EzA 3.9 42 143 fktnDzpjYBUG5a-w_xq01A 4.5 1 9 iPJAN6rJHv92WE2h9b3lAA 3.79 71 732 AWCY8laHjH0-3HMT0LGpUA 4.1 4 57 CXi7I5J-ItLGJNyKPkI5gA 3.58 124 453 3TJcP0stfxjWGsLuGQgQdg 3.1 0 44 hQ98T_hy1CoSWw55zA49VQ 3.89 99 1563 zzpgpo54-_P-4rzzBtOuLQ 3.45 71 470 pU6GoRTcl1rIOi6zMynjog 4.05 5 127 Ps_zkoSnuv2Gy-QIt0jEJg 4.31 13 391 _ICqwy7SW8J6OJBab1HkwA 3.81 19 336 J9HamWsxKorlPGUAXy-M9Q 3.57 7 48 t8Whyn2ZWS34TxHsr2mpbg 4.44 0 9 nRagjGVuSALgQ4KfGLn8Ig 4.16 9 167 djQLJTLA4Tx7TpzYCKIqJQ 3.59 13 443 xxhjX14h8cQyKSuTQFy1Lg 2.0 1 4 a643pisN3QSjofk1Jmlo_Q 2.64 1 19 z5y4ejvC8uaUg5fGEJHbRA 4.25 2 108 DvIlmSleoauEoR3fY0Kf5w 4.02 77 412 t-nB38eHbeFuabXBdJMwvg 4.2 0 4 3gniF5P3L_WcoR8zx7wXxA 4.06 407 914 ICwMfseYkrB0ZEK8tDUOHw 3.61 251 2518 eSlOI3GhroEtcbaD_nFXJQ 3.82 33 207 27wlLX7e52vVEvNA4Ksccw 4.39 21 100 QiDtS54JwTGeH81c-a84WQ 3.95 58 431 rnU1EFMSnVJGrQxrnjaODg 3.64 24 318 AsYMm_O4H-mwmWbmeACDHw 5.0 0 1 PktqNN4YpEzkxsuLwiGkSw 4.95 3 17 tj_j9-8YwYZ7ohOsQD5H_w 3.24 4 87 NmC_ZemjAQ6TvzgeaAuTmA 4.4 4 85 NcUMNz6tAahD6mDmuKwYIA 3.95 20 130 gvKlBHFA6VXb9AksWcPMjw 3.21 8 81 WnwpWcNcJhHi39gdIUfJuQ 3.6 31 231 2Bcq1i1ndSyvYDS8Zn2Oew 2.43 0 6 gTAMqkDSj8z84XN8YvsSJg 3.66 231 1053 d7D4dYzF6THtOx9imf-wPw 3.91 8 108 aQCbHG-3LG6GPLLsf984Rw 4.57 1 26 1a36KbE7XH31Uo4fkmdkqQ 3.54 0 13 tAgzrWAxZivvK8-KqPzNCg 3.84 90 381 DFL9Xl-tS1MH4ZAPchYmjA 5.0 0 1 qB_gBx7eEVVKcy-vaNFInw 5.0 0 14 Kgv4_8tmBIeZmVYu3rUhVg 4.0 0 1 v_OyraTrMO8mVa39ziyrXw 3.76 21 188 jx-BchSqX2PlnMflR62Urw 3.88 1 98 LQbuEFUxqB0Ekt7Ps9ZnJA 4.37 1 27 7wFpWiJMxePaaGiL_c-_IQ 5.0 0 9 _HyT6uRsg8PbCd7nuJA0fA 4.32 3 95 i3dgAM1hWY9UdUCNMDnLXQ 3.46 2 60 uF5V6WYHa38TJU9LFQyjFQ 4.44 2 16 Z_ZkQgFtL2skSyZ9_9NUaQ 4.08 100 1209 bURBDO2lgSrxnth2P7v3Gw 3.72 9 69 o4XHXgKL_UW9g5BV3WZZpA 1.62 1 11 C5pmvrZVeD9jEVWBiyIwzQ 3.81 2 31 A7wZ9ajdlhbMeGIGAlUIbQ 3.49 14 112 wud3mpvvW5yoSB_ZjS-Oig 3.11 2 44 e67TGUfNnz04A1Ahd0tF2A 3.78 272 993 4TCOItk-gIJROyNA5ftZ-Q 3.83 0 22 bZURgbxLW7VHiqk45cafLA 4.75 2 20 jNCv2b6bTP-J-cA_ESbW2w 4.27 9 104 6CVEGPmmgCH4PDGUbeBpKw 3.92 7 81 6e9rJKQC3n0RSKyHLViL-Q 3.84 282 1042 wQ0lKC5BMg3ZvCco8FI1EQ 4.21 63 443 ryf4jg4g3xweyIjkGOY3vg 4.19 8 63 i7dva-DqwjyAtLVc2idhNA 3.88 912 4308 U4INQZOPSUaj8hMjLlZ3KA 3.64 39 376 W1AFbtC37Q1RzdrKS51NmQ 3.81 7 55 -oHBgKNC6xGHIGdoZW3ReQ 3.95 30 293 eBfQ8ABqB7PJ1yl8d6Ll3w 4.02 15 197 88lh7M1G24zM_ALekJ8mzQ 3.92 6 62 KUmin6YNvQZVdrhVED7GAQ 3.45 2 20 B4GZ3kX1TpxJUCkpPqYqng 3.22 0 16 on3cA28Qu-Eh50IuS2iq6w 3.75 124 1525 XkLK2iBsgqF6mWwDfRgqqQ 3.75 2 56 0shsnwv_bUseoK0AMAlRRw 3.84 28 259 SaWQOZm3N43fkJh82glIMQ 2.78 0 9 vGDII1284LVonpfLUN6nTA 3.8 426 1090 Ar3bat-NGasrXDiS7WF8OA 1.0 0 3 LRWg8McG8i9iCY4SOmpa-Q 3.31 0 40 t-CgepilG9t8fpHBdt284w 3.06 15 249 fmPko8NeSgKpb5YwhLJ_gg 4.1 7 90 0caEeLnTD7qENhy4wmUFXg 4.51 11 173 E0TsnBuNAOSnXKiLe18l1A 4.38 23 244 SNQcE_Bc0QAbxFu5F1dTzw 4.0 1 9 KRAGCgnAC0Lmw9YaVSqY7w 4.16 23 21 Fw4UjJ6yBeyPB27Y4wwEUQ 4.14 1 37 jVvKhFgCTW0PgkMbiCkp3A 3.81 6 244 4i4lyXBigT2HShIjw7TbDw 3.0 0 4 B2CkkEX341HLK3zbn3qcgQ 3.73 379 1379 fRJpK_b0rrjpBgRZjvfvgA 5.0 2 5 ethmTQIejtNt715NYme53g 3.21 0 70 xZAmw5gihOVO4duMN2Ju6Q 3.56 54 436 QFrfQw7FH96Vk6PFxxTLcA 4.02 150 1093 NNgQ8fV5ARQgHw-Ob7l50A 4.3 192 398 i_EASSNcEqc1JrfdBjBeVw 3.88 72 178 oiB8fJMd96MNUugca5cvig 3.89 447 2097 lConjPFTZqz4zWELK_EJtw 3.78 1 36 Hl06-Y6fqMRvfbBJ6qmDOA 3.55 63 764 GYMIDghm2k7gSTpyKNid1Q 3.97 15 247 nhtRcOjuycPLDhXXb2MVRA 3.83 49 267 F78tJHr0qW6FsYBtWMmLpA 3.76 12 127 updNAUcQkI9wm2yNoRNubQ 3.72 191 4652 Xj0O2l0bp633ebmG468aZw 3.93 0 13 TUE3NJYN4i7xyGVSIXMLvw 4.35 10 78 FDw1j4PYezkEkdd

#### Reading the Amazon S3 Checkins dataset from JSON format and storing it as Pyspark dataframe

In [6]:
#Reading the Amazon S3 Checkins dataset from JSON format and storing it as Pyspark dataframe

Checkin_df = spark.read.json("dbfs:/mnt/inst767-mount/checkin.json")

display(Checkin_df)

business_id date --1UhMGODdWsrMastO9DZw 2016-04-26 19:49:16, 2016-08-30 18:36:57, 2016-10-15 02:45:18, 2016-11-18 01:54:50, 2017-04-20 18:39:06, 2017-05-03 17:58:02 --6MefnULPED_I942VcFNA 2011-06-04 18:22:23, 2011-07-23 23:51:33, 2012-04-15 01:07:50, 2012-05-06 23:08:42, 2012-06-08 22:43:12, 2012-08-06 23:20:52, 2012-08-19 18:30:44, 2013-01-27 23:49:51, 2013-03-01 01:22:29, 2013-03-23 21:53:47, 2013-03-24 01:11:51, 2013-05-20 00:12:25, 2013-06-29 22:50:57, 2013-07-01 15:58:04, 2013-07-01 22:35:42, 2013-07-28 21:46:49, 2013-08-02 22:06:03, 2013-08-11 18:42:03, 2013-08-23 01:29:56, 2013-09-17 17:40:36, 2013-09-20 23:36:30, 2013-09-24 23:50:18, 2013-10-12 23:11:13, 2013-11-24 18:40:15, 2013-12-12 02:52:54, 2013-12-26 17:33:17, 2013-12-30 00:27:37, 2014-03-28 23:38:23, 2014-04-25 22:48:11, 2014-04-28 22:56:07, 2014-05-03 01:02:47, 2014-05-19 17:08:37, 2014-06-16 00:04:51, 2014-06-22 17:21:27, 2014-07-04 19:13:34, 2014-07-11 15:46:29, 2014-07-25 20:55:48, 2014-08-23 22:27:42, 2014-08-31 01:43:10, 2014-09-06 16:29:55, 2014-09-13 23:34:42, 2014-10-11 23:20:09, 2014-11-19 19:05:56, 2014-11-30 23:27:15, 2015-01-04 01:06:47, 2015-01-04 01:08:08, 2015-01-11 00:16:13, 2015-01-17 23:42:09, 2015-01-17 23:46:42, 2015-01-26 00:05:15, 2015-02-18 17:21:01, 2015-03-22 22:26:09, 2015-03-28 22:47:50, 2015-04-03 21:49:35, 2015-04-05 18:52:21, 2015-04-11 22:59:11, 2015-04-12 22:52:29, 2015-04-24 00:02:22, 2015-05-09 21:45:34, 2015-05-16 22:53:44, 2015-06-07 17:54:51, 2015-07-01 16:24:54, 2015-07-10 22:13:09, 2015-07-11 22:16:37, 2015-07-18 00:27:00, 2015-08-29 23:51:50, 2015-09-07 22:57:51, 2015-09-27 23:54:33, 2015-10-11 22:03:40, 2015-10-12 15:08:23, 2015-10-23 01:34:21, 2015-10-25 00:36:12, 2015-11-09 18:55:17, 2015-11-15 00:01:47, 2015-12-16 19:59:00, 2015-12-27 01:00:59, 2016-01-23 19:05:37, 2016-01-30 23:54:10, 2016-02-07 03:19:01, 2016-02-13 17:49:41, 2016-02-16 00:16:10, 2016-03-27 21:14:50, 2016-04-02 16:29:16, 2016-04-02 17:17:50, 2016-04-16 22:27:48, 2016-04-27 23:54:21, 2016-05-07 21:52:13, 2016-05-21 22:14:00, 2016-06-04 23:06:32, 2016-06-11 22:23:48, 2016-07-01 02:59:31, 2016-07-02 23:01:47, 2016-07-06 22:27:12, 2016-07-08 00:49:30, 2016-07-16 23:53:17, 2016-07-26 17:15:19, 2016-08-01 22:46:32, 2016-08-02 00:14:10, 2016-08-18 03:19:16, 2016-08-20 12:47:15, 2016-08-21 12:24:31, 2016-09-15 20:31:53, 2016-10-03 01:04:15, 2016-10-03 01:04:25, 2016-11-26 00:48:51, 2016-12-24 17:56:29, 2016-12-31 18:29:26, 2017-01-09 01:07:12, 2017-01-15 03:53:00, 2017-01-15 17:30:16, 2017-01-28 00:44:48, 2017-02-10 20:18:01, 2017-02-18 23:13:18, 2017-02-19 00:30:24, 2017-02-20 02:04:48, 2017-04-16 22:46:55, 2017-04-27 04:38:34, 2017-05-13 22:51:49, 2017-05-19 23:03:19, 2017-05-31 22:46:11, 2017-05-31 22:46:33, 2017-07-28 23:38:19, 2017-08-13 23:42:59, 2017-08-17 23:27:33, 2017-09-03 17:30:25, 2017-09-03 22:59:25, 2017-09-16 21:12:41, 2017-09-18 00:36:34, 2017-09-28 23:28:02, 2017-10-01 13:02:01, 2017-10-08 00:00:05, 2017-10-08 15:07:36, 2017-10-09 00:44:22, 2017-10-15 22:31:47, 2017-10-17 23:31:26, 2017-10-17 23:32:10, 2017-11-04 22:48:12, 2017-11-10 20:50:25, 2017-12-17 23:02:32, 2017-12-21 00:55:13, 2017-12-29 01:53:12, 2017-12-29 01:53:52, 2018-01-26 00:47:30, 2018-03-30 16:49:10, 2018-04-07 16:27:21, 2018-04-24 23:45:19, 2018-05-05 18:27:12, 2018-05-05 22:27:18, 2018-05-14 23:47:27, 2018-05-20 23:49:45, 2018-05-25 16:39:21, 2018-06-04 21:40:47, 2018-06-04 21:40:58, 2018-06-12 22:27:30, 2018-06-20 22:53:27, 2018-07-05 16:15:18, 2018-07-08 18:40:13, 2018-07-08 20:41:46, 2018-07-18 20:58:49, 2018-07-24 23:35:44, 2018-08-09 00:08:56, 2018-08-20 22:29:00, 2018-08-31 17:47:54, 2018-09-13 23:08:09, 2018-09-15 22:16:51, 2018-10-21 18:09:02, 2018-10-21 22:58:14 --7zmmkVg-IMGaXbuVd0SQ 2014-12-29 19:25:50, 2015-01-17 01:49:14, 2015-01-24 20:31:57, 2015-02-07 22:38:13, 2015-02-15 00:02:28, 2015-02-21 20:23:14, 2015-02-27 23:09:22, 2015-02-27 23:09:25, 2015-04-19 00:54:07, 2015-05-01 21:54:22, 2015-05-09 00:08:34, 2015-05-30 22:27:49, 2015-06-05 23:10:19, 2015-06-06

#### Reading the Amazon S3 Reviews dataset from JSON format and storing it as Pyspark dataframe

In [8]:
# #Reading the Amazon S3 Reviews dataset from JSON format and storing it as Pyspark dataframe

# reviews_schema = StructType([StructField('business_id', StringType(), True),
#                             StructField('cool', IntegerType(), True),
#                             StructField('date', TimestampType(), True),
#                             StructField('funny', IntegerType(), True),
#                             StructField('review_id', StringType(), True),
#                             StructField('stars', IntegerType(), True),
#                             StructField('text', StringType(), True),
#                             StructField('useful', IntegerType(), True),
#                             StructField('user_id', StringType(), True)])

reviews_df = spark.read.json("dbfs:/mnt/inst767-mount/review.json")

reviews_df = reviews_df.withColumn('cool_integer', reviews_df['cool'].cast(IntegerType())).drop('cool')
reviews_df = reviews_df.withColumn('funny_integer', reviews_df['funny'].cast(IntegerType())).drop('funny')
reviews_df = reviews_df.withColumn('stars_integer', reviews_df['stars'].cast(IntegerType())).drop('stars')
reviews_df = reviews_df.withColumn('useful_integer', reviews_df['useful'].cast(IntegerType())).drop('useful')

reviews_df = reviews_df.withColumnRenamed('cool_integer', 'cool')
reviews_df = reviews_df.withColumnRenamed('funny_integer', 'funny')
reviews_df = reviews_df.withColumnRenamed('stars_integer', 'stars')
reviews_df = reviews_df.withColumnRenamed('useful_integer', 'useful')

display(reviews_df)

business_id date review_id text user_id cool funny stars useful ujmEBvifdJM6h6RLv4wQIg 2013-05-07 04:34:36 Q1sbwvVQXV2734tPgoKj4Q Total bill for this horrible service? Over $8Gs. These crooks actually had the nerve to charge us $69 for 3 pills. I checked online the pills can be had for 19 cents EACH! Avoid Hospital ERs at all costs. hG7b0MtEbXx5QzbzE6C_VA 0 1 1 6 NZnhc2sEQy3RmzKTZnqtwQ 2017-01-14 21:30:33 GJXCdrto3ASJOqKeVWPi6Q I *adore* Travis at the Hard Rock's new Kelly Cardenas Salon! I'm always a fan of a great blowout and no stranger to the chains that offer this service; however, Travis has taken the flawless blowout to a whole new level! 

Travis's greets you with his perfectly green swoosh in his otherwise perfectly styled black hair and a Vegas-worthy rockstar outfit. Next comes the most relaxing and incredible shampoo -- where you get a full head message that could cure even the very worst migraine in minutes --- and the scented shampoo room. Travis has freakishly strong fingers (in a good way) and use the perfect amount of pressure. That was superb! Then starts the glorious blowout... where not one, not two, but THREE people were involved in doing the best round-brush action my hair has ever seen. The team of stylists clearly gets along extremely well, as it's evident from the way they talk to and help one another that it's really genuine and not some corporate requirement. It was so much fun to be there! 

Next Travis started with the flat iron. The way he flipped his wrist to get volume all around without over-doing it and making me look like a Texas pagent girl was admirable. It's also worth noting that he didn't fry my hair -- something that I've had happen before with less skilled stylists. At the end of the blowout & style my hair was perfectly bouncey and looked terrific. The only thing better? That this awesome blowout lasted for days! 

Travis, I will see you every single time I'm out in Vegas. You make me feel beauuuutiful! yXQM5uF2jS6es16SJzNHfg 0 0 5 0 WTqjgwHlXbSFevF32_DJVw 2016-11-09 20:09:03 2TzJjDVDEuAW6MR5Vuc1ug I have to say that this office really has it together, they are so organized and friendly! Dr. J. Phillipp is a great dentist, very friendly and professional. The dental assistants that helped in my procedure were amazing, Jewel and Bailey helped me to feel comfortable! I don't have dental insurance, but they have this insurance through their office you can purchase for $80 something a year and this gave me 25% off all of my dental work, plus they helped me get signed up for care credit which I knew nothing about before this visit! I highly recommend this office for the nice synergy the whole office has! n6-Gk65cPZL6Uz8qRm3NYw 0 0 5 3 ikCg8xy5JIg_NGPx-MSIDA 2018-01-09 20:56:38 yi0R0Ugj_xUx_Nek0-_Qig Went in for a lunch. Steak sandwich was delicious, and the Caesar salad had an absolutely delicious dressing, with a perfect amount of dressing, and distributed perfectly across each leaf. I know I'm going on about the salad ... But it was perfect.

Drink prices were pretty good.

The Server, Dawn, was friendly and accommodating. Very happy with her.

In summation, a great pub experience. Would go again! dacAIZ6fTM6mqwW5uxkskg 0 0 5 0 b1b1eb3uo-w561D0ZfCEiQ 2018-01-30 23:07:38 11a8sVPMUFtaC7_ABRkmtw Today was my second out of three sessions I had paid for. Although my first session went well, I could tell Meredith had a particular enjoyment for her male clients over her female. However, I returned because she did my teeth fine and I was pleased with the results. When I went in today, I was in the whitening room with three other gentlemen. My appointment started out well, although, being a person who is in the service industry, I always attend to my female clientele first when a couple arrives. Unbothered by those signs, I waited my turn. She checked on me once after my original 30 minute timer to ask if I was ok. She attended my boyfriend on numerous occasions, as well as the other men, and woul

In [9]:
@udf(returnType=IntegerType())
def word_count(col):
  return len(col)

reviews_df = reviews_df.withColumn('review_len', word_count('text'))

In [10]:
reviews_df.count()

Out[ 5 ]: 6685900

#### Reading the Amazon S3 Tips dataset from JSON format and storing it as Pyspark dataframe

In [12]:
#Reading the Amazon S3 Tips dataset from JSON format and storing it as Pyspark dataframe

tips_schema = StructType([StructField('business_id', StringType(), True),
                         StructField('compliment_count', IntegerType(), True),
                         StructField('date', TimestampType(), True),
                         StructField('text', StringType(), True),
                         StructField('user_id', StringType(), True)])

tips_df = spark.read.json("dbfs:/mnt/inst767-mount/tip.json")

display(tips_df)

business_id compliment_count date text user_id VaKXUpmWTTWDKbpJ3aQdMw 0 2014-03-27 03:51:24 Great for watching games, ufc, and whatever else tickles yer fancy UPw5DWs_b-e2JRBS-t37Ag OPiPeoJiv92rENwbq76orA 0 2013-05-25 06:00:56 Happy Hour 2-4 daily with 1/2 price drinks and slushes AND after 8 half price shakes. They actually have a peanut butter and bacon shake. Ocha4kZBHb4JK0lOWvE0sg 5KheTjYPu1HcQzQFtm4_vw 0 2011-12-26 01:46:17 Good chips and salsa. Loud at times. Good service. Bathrooms AWFUL. So that tanks my view on this place. jRyO2V1pA4CdVVqCIOPc1Q TkoyGi8J7YFjA6SbaRzrxg 0 2014-03-23 21:32:49 The setting and decoration here is amazing. Come check out the waterfall fountain in the middle! FuTJWFYm4UKqewaosss1KA AkL6Ous6A1atZejfZXn1Bg 0 2012-10-06 00:19:27 Molly is definately taking a picture with Santa lols LUlKtaM3nXd-E4N4uOk_fQ kj1p6NwUGROOoqNySf0I1Q 0 2011-12-31 18:02:42 It's true! The drunken noodles are outrageous! iAd8XaHxv05iXyEiZ62Ibw 0hudPyuCBlKg79OwKBw-eQ 0 2012-10-11 23:06:21 Only worth a visit in the summer time, to take advantage of the huge sun soaked patio. w8p4JW6-ERsbg8aB5wjEAg r49iBfbnfoK7yt4rdsL_7g 0 2016-01-05 06:39:33 Hands down best AYCE in town! Love it! CaFbX7topxdLpBJ_SNDfGQ YCRCFBr6myPS49on2aS2pQ 0 2017-03-13 03:29:40 Sat in the drive thru this afternoon for 30 minutes and then was handed the wrong coffee. Booooo, I'm seriously here every day and this was the first bad experience VLy6l8L72adD7iTBNqiPXw RTBIiq-fJUXRsrzbL4MCqw 0 2013-02-08 20:55:15 Okay so I had a groupon for a nearby service center, but their wait time was 3 hours! Once again, I find myself back at this Brake Masters. Idk why I bother with anywhere else; This place is great! zrvk0-B91ahJRSB-UcAmIA qrSsS0pk7SL67MP5nN8tlg 0 2013-12-22 05:10:12 More parking in the back of the restaurant 8zXgNCkusOHMwh5Tj_8yCQ oGASRzKGpuiP12ilQH_nKg 0 2010-03-04 15:41:16 Best pretzels this side of the Rhein. Wash down with the Franziskaner Weissbier. NXXC2iU0o3tDVu6YNaW3Ww 63bHLJUomC22Xdm3IjgBtw 0 2011-10-18 18:29:05 Having the yellow curry, summer rolls and a coke. I would recommend the rolls but the curry was incredible! DfvT4F5Eqx9Xr3Ei3GYWPg wZhB4U003eg2GQ-F7D2D4A 0 2016-08-12 22:18:07 When you receive the bag of seafood tie it up and then mix it up that way all the flavours get into the seafood. As well for the owner play less Drake music please and thank you when I'm here. :D Congrats Guys oIHhfloe5VQamDFDB2dr1Q Cni2l-VKG_pdospJ6xliXQ 0 2011-10-09 03:43:39 2nd stop for the pub-crawl! Yay! NEN5RFpZp7DE6K1PK2KZzg EZZjaiV8ik05NUepqdeP2A 0 2018-02-14 21:35:49 Really delicious food and amazing service. Fzz-0v1yHLaWuTV64b1miA xZfPdAYeimiruXuGR4nSUA 0 2011-04-21 22:43:28 Dinner!! CbmNBkKa9QKNxPiN_whFUw D2nfOrnJ2OBlX_428sKyMg 0 2011-12-30 17:10:16 Long lines at lunch!! 3KkT6SmPFLGvBS1pnDBr8g C7JaaErXLB3B3486LfWg5w 0 2013-02-17 06:22:49 Go somewhere else to buy a car or mini van.
Rude, assuming sales staff; they are not going to lower the price on a vehicle, The black sales guy is unprofessional and barely knows his job; he is rude and insults customers. kMcz3zQgNjZYV65qY9ztGA j9I2YkFCOKyAEb_3FbFqUA 0 2011-04-09 18:58:36 #poutinecrawl #yyc stop #1 JnHaPHkRO2_8V-DysmIBVw LrO_Xy6lfpbTgFoJcOjY4w 0 2015-05-21 01:13:24 I love the gourmet veggie pizza!! EZbvMdvCA2D9vF6VjILYXA 0PVxodALQu-soL5J8bjerQ 0 2012-07-24 16:24:09 If there's a more authentic breakfast place in Pittsburgh, I haven't found it. Ritter's is comfort food at its best! pDAqvfflIM4AM23VRpqAaw cnfYugAYBFKgwDCTAVdViA 0 2015-05-29 04:25:09 No gGlFgp4nXNL5azpUtLK05w 1l7gJx3BVWBZ8Wx1vPCkeA 0 2013-11-30 04:03:27 New Dr Who! He talks with an accent, " I'm the Doctor" Oui Garcon! HmILc-lgVKZS7mWNdYCSJw 7sPNbCx7vGAaH7SbNPZ6oA 0 2012-08-02 06:25:54 Late night burger cravings... lesnCKZUYH554j-EDZBlTw PEb1Hm0kQ52cObjPAE6nFQ 0 2014-09-06 23:29:08 Cash only! ATM on site alUuOskFSl1bODjnce2PpQ i6G3zsEJIqpGktMWyffXjw 0 2013-12-19 21:29:53 Holiday party hf27xTME3EiCp6NL6VtWZQ XP0YZRa6Un25QaOH2g1ivA 0 2011-12-30

#### Reading the Amazon S3 Business dataset from JSON format and storing it as Pyspark dataframe

In [14]:
#Reading the Amazon S3 Business dataset from JSON format and storing it as Pyspark dataframe

business_schema = StructType([StructField('address', StringType(), True),
                             StructField('attributes', StructType(), True),
                             StructField('business_id', StringType(), True),
                             StructField('categories', StringType(), True),
                             StructField('city', StringType(), True),
                             StructField('hours', StructType(), True),
                             StructField('is_open', IntegerType(), True),
                             StructField('latitude', FloatType(), True),
                             StructField('longitude', FloatType(), True),
                             StructField('name', StringType(), True),
                             StructField('postal_code', StringType(), True),
                             StructField('review_count', IntegerType(), True),
                             StructField('stars', FloatType(), True),
                             StructField('state', StringType(), True)])

business_df = spark.read.json("dbfs:/mnt/inst767-mount/business.json", schema = business_schema)

business_df = business_df.withColumnRenamed('review_count', 'business_review_count')

display(business_df)

address attributes business_id categories city hours is_open latitude longitude name postal_code business_review_count stars state 2818 E Camino Acequia Drive List() 1SWheh84yJXfytovILXOAQ Golf, Active Life Phoenix null 0 33.522144 -112.01848 Arizona Biltmore Golf Club 85016 5 3.0 AZ 30 Eglinton Avenue W List() QXAEGFB4oINsVuTFxEYKFQ Specialty Food, Restaurants, Dim Sum, Imported Food, Food, Chinese, Ethnic Food, Seafood Mississauga List() 1 43.6055 -79.65229 Emerald Chinese Restaurant L5R 3E7 128 2.5 ON 10110 Johnston Rd, Ste 15 List() gnKjwL_1w79qoiV3IC_xQQ Sushi Bars, Restaurants, Japanese Charlotte List() 1 35.092564 -80.85913 Musashi Japanese Restaurant 28210 170 4.0 NC 15655 W Roosevelt St, Ste 237 null xvX2CttrVhyG2z1dFg_0xw Insurance, Financial Services Goodyear List() 1 33.455612 -112.3956 Farmers Insurance - Paul Lorenz 85338 3 5.0 AZ 4209 Stuart Andrew Blvd, Ste F List() HhyxOkGAM07SRYtlQ4wMFQ Plumbing, Shopping, Local Services, Home Services, Kitchen & Bath, Home & Garden, Water Heater Installation/Repair Charlotte List() 1 35.19001 -80.88722 Queen City Plumbing 28217 4 4.0 NC Credit Valley Town Plaza, F2 - 6045 Creditview Rd List() 68dUKd8_8liJ7in4aWOSEA Shipping Centers, Couriers & Delivery Services, Local Services, Printing Services Mississauga List() 1 43.599476 -79.711586 The UPS Store L5V 0B1 3 2.5 ON 20 Douglas Woods Drive Southeast List() 5JucpCfHZltJh5r1JabjDg Beauty & Spas, Hair Salons Calgary null 1 50.943645 -114.00183 Edgeworxx Studio T2Z 1K4 7 3.5 AB 4545 E Tropicana Rd Ste 8, Tropicana List() gbQN7vr_caG_A1ugSmGhWg Hair Salons, Hair Stylists, Barbers, Men's Hair Salons, Cosmetics & Beauty Supply, Shopping, Beauty & Spas Las Vegas List() 1 36.099873 -115.07458 Supercuts 89121 3 3.5 NV 5940 W Union Hills Dr List() Y6iyemLX_oylRpnr38vgMA Nail Salons, Beauty & Spas, Day Spas Glendale List() 0 33.654816 -112.18857 Vita Bella Fine Day Spa 85308 8 5.0 AZ 21689 Lorain Rd List() 4GBVPIYRvzGh4K4TkRQ_rw Beauty & Spas, Nail Salons, Day Spas, Massage Fairview Park List() 1 41.440826 -81.854095 Options Salon & Spa 44126 8 4.5 OH 1210 8th Street SW, Unit 220 List() fcXOEZdXYeZqnQ3lGlOXmg Local Services, Professional Services, Computers, Shopping, Home Services, IT Services & Computer Repair, Internet Service Providers, Web Design Calgary List() 1 51.04177 -114.08111 Nucleus Information Service T2R 1L3 5 2.0 AB 2450 E Indian School Rd List() 1Dfx3zM-rW4n-31KeC8sJg Restaurants, Breakfast & Brunch, Mexican, Tacos, Tex-Mex, Fast Food Phoenix List() 1 33.495193 -112.02859 Taco Bell 85016 18 3.0 AZ 119 Landings Dr, Ste 101 List() 5t3KVdMnFgAYmSl1wYLhmA Bars, Nightlife, Pubs, Barbers, Beauty & Spas, Irish Pub Mooresville List() 1 35.52741 -80.868004 The Kilted Buffalo Langtree 28117 9 3.5 NC 5981 Andrews Rd List() fweCYi8FmbJXHCqLnwuk8w Italian, Restaurants, Pizza, Chicken Wings Mentor-on-the-Lake List() 1 41.70852 -81.35956 Marco's Pizza 44060 16 4.0 OH 4145 Erie St List() -K4gAv8_vjx8-2BxkVeRkA Bakeries, Food Willoughby List() 1 41.63986 -81.406395 Baby Cakes 44094 7 3.0 OH 1455 16th Avenue List() A98xW4qb7vOTguggHFs7Ng Fitness & Instruction, Active Life, Yoga Richmond Hill List() 1 43.861504 -79.3885 Hot Yoga Wellness L4B 3G6 4 4.0 ON 4848 E Cactus Rd, Ste 100 List() giC3pVVFxCRR89rApqklyw Hair Stylists, Beauty & Spas, Hair Salons, Men's Hair Salons Scottsdale List() 1 33.60007 -111.97737 Knot Salon 85254 5 5.0 AZ 1775 E Tropicana Ave, Ste 29 List() PZ-LZzSlhSe9utkQYU8pFg Restaurants, Italian Las Vegas null 0 36.100018 -115.128525 Carluccio's Tivoli Gardens 89119 40 4.0 NV List() nh_kQ16QAoXWwqZ05MPfBQ Event Planning & Services, Photographers, Professional Services Las Vegas List() 1 36.11655 -115.08811 Myron Hensel Photography 89121 21 5.0 NV 445 King Street W, Suite 101 List() zSpQmEBvRe3IhTUlMSA6HQ Trainers, Health & Medical, Active Life, Physical Therapy, Gyms, Fitness & Instruction Toronto List() 1 43.645042 -79.3958 Totum Life Science M5V 1K4 23 4.0 ON 450 Fremont St, Ste 179 List() dFMxzHygTy6F873843dHAA Arcades

### Preprocessing the business dataframe

In [16]:
#UDF that counts # of rows and # of columns
def shape(df):
  return [df.count(), len(df.columns)]

#Drop the attributes and hours columns, then check new schema
business_df = business_df.drop('attributes')
business_df = business_df.drop('hours')

#Checking the # of null/missing values in the Business dataset
from pyspark.sql.functions import isnan, when, count, col
business_df.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in business_df.columns]).show()

# Drop rows with null values in categories column
business_df = business_df.dropna(subset = 'categories')
# business_df.show(5)

#Only keeping the businesses that are restaurants or are food related
from pyspark.sql.functions import udf
from pyspark.sql.types import BooleanType

@udf(returnType=BooleanType())
def filter_restaurants(col):
  for category in col.split(','):
    if 'restaurant' in category.lower() or 'food' in category.lower():
      return True
  return False

@udf(returnType=BooleanType())
def filter_non_restaurants(col):
  category = ' '.join(col.split(','))
  if 'restaurant' not in category.lower() and 'food' not in category.lower():
    return True
  return False

#Reviewing businesses that are restaurants and are food related
business_df_restaurants = business_df.filter(filter_restaurants('categories'))

#Reviewing businesses that are not restaurants and are not food related
business_df_nonRestaurants = business_df.filter(filter_non_restaurants('categories'))

#Determining the # of unique categories from our restaurants dataframe as well as our non-restaurants non-restaurants dataframe, in case we find other keywords that should be used
def get_unique(df):
  """
  Returns a list of unique categories from the df
  """
  unique_categories = {}
  
  for row in df.select('categories').rdd.collect():
    categories = row.asDict()['categories']
    for category in categories.split(','):
      try:
        unique_categories[category.lower().strip()] += 1
      except:
        unique_categories[category.lower().strip()] = 0
        
  return unique_categories
    
unique_category_nonRestaurants = get_unique(business_df_nonRestaurants)
unique_category_restaurants = get_unique(business_df_restaurants)

print('Number of unique categories in restaurants df are {}'.format(len(unique_category_restaurants)))  
print('Number of unique categories in non restaurants df are {}'.format(len(unique_category_nonRestaurants))) 

+-------+-----------+----------+----+-------+--------+---------+----+-----------+---------------------+-----+-----+
address|business_id|categories|city|is_open|latitude|longitude|name|postal_code|business_review_count|stars|state|
+-------+-----------+----------+----+-------+--------+---------+----+-----------+---------------------+-----+-----+
 0| 0| 482| 0| 0| 0| 0| 0| 0| 0| 0| 0|
+-------+-----------+----------+----+-------+--------+---------+----+-----------+---------------------+-----+-----+

Number of unique categories in restaurants df are 880
Number of unique categories in non restaurants df are 1044

In [17]:
display(business_df_restaurants.select('state').distinct())

state AZ SC BAS VA QC BC NV WI CA NE NC VT IL XGL WA AL XGM OH NM PA NY ON AB CON TX XWY FL AR

In [18]:
business_df_restaurants.createOrReplaceTempView('business_restaurants_VIEW')

In [19]:
%sql select state, count(business_id) from business_restaurants_VIEW group by state order by count(business_id) desc

state count(business_id) ON 18387 AZ 14792 NV 10065 OH 6777 QC 6651 NC 5550 PA 5061 AB 3845 WI 2133 IL 813 SC 493 NY 13 AL 2 XGM 2 XWY 2 BAS 1 VA 1 BC 1 VT 1 CA 1 NE 1 WA 1 NM 1 CON 1 TX 1 AR 1 XGL 1 FL 1

### We choose a subset of the data. Select the following states: AZ, OH

In [21]:
filtered_business_df = business_df_restaurants.filter((business_df_restaurants.state == 'AZ') | (business_df_restaurants.state == 'OH'))

display(filtered_business_df)

address business_id categories city is_open latitude longitude name postal_code business_review_count stars state 2450 E Indian School Rd 1Dfx3zM-rW4n-31KeC8sJg Restaurants, Breakfast & Brunch, Mexican, Tacos, Tex-Mex, Fast Food Phoenix 1 33.495193 -112.02859 Taco Bell 85016 18 3.0 AZ 5981 Andrews Rd fweCYi8FmbJXHCqLnwuk8w Italian, Restaurants, Pizza, Chicken Wings Mentor-on-the-Lake 1 41.70852 -81.35956 Marco's Pizza 44060 16 4.0 OH 4145 Erie St -K4gAv8_vjx8-2BxkVeRkA Bakeries, Food Willoughby 1 41.63986 -81.406395 Baby Cakes 44094 7 3.0 OH 709 W Ray Rd GWO87Y-IqL54_Ijx6hTYAQ Food, Desserts, Juice Bars & Smoothies, Ice Cream & Frozen Yogurt Gilbert 0 33.320385 -111.80465 Bruster's Real Ice Cream 85233 57 4.5 AZ 17025 N Scottsdale Rd, Ste 110 q2KtxnPa6rPSpAlMbg9l8g Desserts, Food, Cupcakes, Bakeries Scottsdale 1 33.64031 -111.92453 Nothing Bundt Cakes 85255 174 4.0 AZ 3101 W Northern Ave c-BELKj0SvNhBesQMf-bKw Convenience Stores, Automotive, Food, Gas Stations, Grocery Phoenix 1 33.55285 -112.12598 Circle K 85051 3 2.5 AZ 13843 N Tatum Blvd, Ste 15 44YFU284Z3KDEy25QyVoUw Chinese, Restaurants Phoenix 1 33.61302 -111.977036 Nee House Chinese Restaurant 85032 269 3.5 AZ 664 Broadway Ave iXkqd9uNods7YnxrnBq_RA Home Decor, Cosmetics & Beauty Supply, Health & Medical, Home & Garden, Herbal Shops, Beauty & Spas, Food, Nurseries & Gardening, Spiritual Shop, Shopping Bedford 1 41.39194 -81.536316 Spirit Apothecary 44146 10 4.5 OH 402 Great Northern Blvd 7aLkFEBnL1LJmQdcuaovuQ Restaurants, Pubs, Bars, Nightlife, American (Traditional), Beer Gardens North Olmsted 1 41.416588 -81.90437 Ohio Beer Garden 44070 8 4.0 OH 6625 Dean Memorial Pkwy 0lFAD4CuWcQVl9u3-lRaCQ Pubs, Restaurants, Bars, Event Planning & Services, American (Traditional), Nightlife, Lounges, Venues & Event Spaces, Sports Bars Hudson 1 41.26113 -81.50346 Cruisers Bar and Grill 44236 12 3.5 OH 1789 W Jefferson ysfeDcLAYk_MVzfBmyiSTg Restaurants, Food, Cafes Phoenix 1 33.446804 -112.09713 Vals Getaway DES Cafeteria 85007 14 3.0 AZ 9133 W Thunderbird Rd, Ste 107 Q1GhjqlLENaT383k9Ex5wg Donuts, Coffee & Tea, Juice Bars & Smoothies, Food Peoria 1 33.609215 -112.255615 Daily Donut 85381 33 4.5 AZ 95 W Boston r8764MtYyt8JhxMvrfM_xQ American (New), Bars, Wine Bars, Nightlife, Restaurants Chandler 0 33.302094 -111.84261 Vintage 95 85225 320 4.0 AZ 3140 S Gilbert Rd, Ste 3 voZnDQs6Hs3YpNcS-9TALg Restaurants, Mexican Chandler 0 33.261326 -111.79082 New Mexican Grill 85286 84 4.0 AZ 550 N Hayden Rd nsNONDHbV7Vudqh21uicqw Seafood, Restaurants Scottsdale 1 33.454285 -111.90941 Salt Cellar 85257 526 3.5 AZ 3415 West Glendale Ave, Bldg 25A Rs8Wi4OEjeOX7LVlzsXDOA Restaurants, Mexican, Sushi Bars Phoenix 1 33.537163 -112.13293 Sushi Mocorito 85051 9 3.0 AZ 2765 N Scottsdale Rd, Ste 105 MhnihE0alud0ereVInSt8Q Chinese, Restaurants Scottsdale 1 33.478752 -111.92548 Yummy Yummy Chinese Restaurant 85257 188 3.0 AZ 6185 W Chandler Blvd FDEm-c3NAXnTVtl-hgzAhA Burgers, Restaurants Chandler 0 33.304764 -111.94808 Heart Attack Grill 85226 104 3.0 AZ 12700 Shaw Ave OwXMxqxIy4YoprAjnoUoiA Barbeque, Restaurants Cleveland 1 41.54089 -81.59533 B & M Bar-B-Que Shaw 44108 4 3.5 OH 3460 E Southern Ave, Ste 109 Sd75ucXKoZUM2BEfBHFUOg Chinese, Restaurants Mesa 0 33.394863 -111.756035 China Gourmet 85204 13 3.0 AZ 8870 Mentor Ave U3-kxz7NWq4ix4bPmKKQ0w Ethnic Food, Specialty Food, Food, Restaurants, Vegetarian, Mediterranean, Middle Eastern Mentor 1 41.67386 -81.32282 Aladdin's Eatery 44060 47 4.5 OH 1008 E Camelback Rd dUffgo9Lh_Vk9TLuFR5ywg Restaurants, Pizza, Sandwiches, Italian Phoenix 1 33.50951 -112.06024 Oregano's Pizza Bistro 85014 563 3.5 AZ 1930 W Buckeye Rd c7JoAt6a3Ufkpn3TrGU23A Mexican, Restaurants Phoenix 1 33.436985 -112.101265 Santanas Mexican Food 85009 6 3.0 AZ 25800 Central Pwky vwntGW400t5WG0ubjuaz5g Barbeque, Restaurants Beachwood 0 41.46759 -81.49326 The Pit 44122 5 2.0 OH 2340 E Baseline Rd vg4ynLZ0yJ89pT4s_CEMzQ Fast Food, Restaurants, Burgers, Food Phoenix 1 33.3787 -112.03101 Five Guys 8

In [22]:
shape(filtered_business_df)

Out[ 12 ]: [21569, 12]

### Join the Review, Business and Users dataframes

In [24]:
#Checking unique user_id count, making sure there are no duplicate records. They are they same, but the code is commented out so the cell runs faster
#Users_refined_df.select("user_id").distinct().count()
#Users_refined_df.select("user_id").count()

#Rename the stars column in both the review and business dataframes, so that there is no confusion when joining
reviews_df2 = reviews_df
reviews_df2 = reviews_df2.withColumnRenamed('stars', 'review_stars')
business_df_restaurants2 = filtered_business_df
business_df_restaurants2 = business_df_restaurants2.withColumnRenamed('stars', 'business_stars')

#Making a copy of the Users dataframe
#Users_refined_df2 = Users_refined_df

#Join the Review dataframe with the Business dataframe
#review_analysis_df = reviews_df2
review_analysis_df = reviews_df2.join(business_df_restaurants2, 'business_id', 'inner')

#Join the above review_analysis_df dataframe with the Users dataframe, so that we have one combined data frame that is per review
review_analysis_df = review_analysis_df.join(Users_refined_df, 'user_id', 'inner')




In [25]:
display(review_analysis_df)

user_id business_id date review_id text cool funny review_stars useful address categories city is_open latitude longitude name postal_code business_review_count business_stars state average_stars fans user_review_count -3i9bhfvrM3F1wsC9XIB8g pSQFynH1VxkfSmehRXlZWw 2016-11-18 22:03:29 UxxjKGFUJOlTvAXDb-kwIg Fantastic pizza. Small but interesting beer selection. Good, friendly service.
I got the biancoverde pizza, a white pizza with fresh mozzarella, ricotta and a ton of fresh arugula. Delicious. 2 2 5 4 623 E Adams St Sandwiches, Restaurants, Pizza, Salad, Tapas/Small Plates, Italian Phoenix 1 33.44916 -112.065636 Pizzeria Bianco 85004 2276 4.0 AZ 4.07 97 652 -3i9bhfvrM3F1wsC9XIB8g ghpFh6XpH1TYZhjAGdx-xw 2016-11-18 22:11:54 SQSKmO5D97yIYC0S2RbR_w Really quick for lunch, very tasty pizzas and salads, at a great price.

Staff seems to be a bit reluctant to add "extra" ingredients even if the pizza is meatless. The make your own pizzas are one price. My colleague wanted a simple pizza with extra mushrooms, and the preparer kept adding one or two extra 'shrooms at my friend's urging, and looking back at the manager cautiously. In the meantime, I had a pie with two cheeses, two meats and several different veggies, and nobody batted an eye. 3 2 4 4 3110 N Central Ave Italian, Salad, Food, Pizza, Restaurants Phoenix 1 33.4838 -112.07524 Fired Pie 85012 232 4.0 AZ 4.07 97 652 -55DgUo52I3zW9RxkZ-EAQ 3qlqzQrwh8hjBltlgFgsJQ 2015-11-11 04:32:22 NFgnyyp2Kl1nlWIEkXZs4w Great place for late night food. College crowd/seen, usually loud. So that is what to expect. But, with that being said, It is great food & drink. I love go there b/c everyplace else has no late night food. It is one of my go to late night food and drink. Fun place. 0 0 4 0 1011 N 3rd St Restaurants, Mexican Phoenix 0 33.45917 -112.06899 Paz Cantina 85004 264 4.0 AZ 4.59 1 47 -55DgUo52I3zW9RxkZ-EAQ 9O-L6F0cMfNmE5i07pN_xQ 2016-08-13 23:40:11 iOTTR1df4vYAtE9WnOHtoA Great cake. Chocolate was perfect, and they are open on Sunday's. Which is really nice for Sunday birthday parties. Def going to come back. Thank you guys for the great cake. 1 0 4 0 15414 N 7th St, Ste 6 Breakfast & Brunch, Food Trucks, Comfort Food, Restaurants, Waffles, Coffee & Tea, Bakeries, Food Phoenix 1 33.626354 -112.06639 Mamma Toledo's The Pie Hole 85022 180 4.0 AZ 4.59 1 47 -55DgUo52I3zW9RxkZ-EAQ nn4ZkIZTCd7jJhxs-P9tHA 2016-12-17 16:06:29 zqwxKCkD2PfTRRft5Nv0sg Fun, easy, good 50's Diner. Come here for fun Diner experience. 
If you want fancy brunch with the girls go somewhere else. 
If you have a hang over and had fun last night with the girls and need to share bar stories come here. 0 0 4 0 5220 N 16th St Diners, Breakfast & Brunch, Restaurants, Burgers Phoenix 1 33.51346 -112.047844 5 & Diner 85016 300 3.5 AZ 4.59 1 47 -55DgUo52I3zW9RxkZ-EAQ VuYF1vGKLjEFaQfL4Ypwqg 2017-07-29 02:06:31 p1KItC5NgZEvkJksFtUdRQ Sat at the bar. Ordered a whiskey sour with egg whites. You should try it. Perfect with their food. Came out fast and perfect. 0 0 5 0 928 E Pierce St Breakfast & Brunch, Tacos, Cafes, Bars, Restaurants, Nightlife, Mexican Phoenix 1 33.456028 -112.060844 Gallo Blanco 85006 195 4.0 AZ 4.59 1 47 -55DgUo52I3zW9RxkZ-EAQ CYWRPE-1IHPBb-zfFO6KRg 2015-11-11 18:27:46 aTeezUJusRSqzrFcUdiuCA Great, rich, European home cooked type meals. Like my Dad makes. Along with awesome cocktails, and decent wine list. Younger business, and local downtown eclectic working professionals (aka gay guys with great taste in food and dress :) ) More dress up a bit dinning, with relaxed atmosphere and good food. Late night food as well !!! Have been back many times. 0 0 5 0 2601 N Central Ave Breakfast & Brunch, Burgers, Mediterranean, Spanish, Modern European, Sandwiches, Comfort Food, Cocktail Bars, American (Traditional), Tapas/Small Plates, Restaurants, Bars, Nightlife Phoenix 0 33.476837 -112.07359 Corduroy 85004 156 4.0 AZ 4.59 1 47 -55DgUo52I3zW9RxkZ-EAQ 3awTUGMdUVrwEBkFFOxn9Q 2016-10-27 04:17:17 TlmdmL1IgVfKQ6BpUdcJ7w Great

In [26]:
shape(review_analysis_df)

Out[ 15 ]: [1545286, 23]

### Vader Sentiment

In [28]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

analyser = SentimentIntensityAnalyzer()

# positive sentiment - compound score >= 0.05
# neutral sentiment - compound score (-0.05, +0.05)
# negative sentiment - compund score <= -0.05

User defined function to calculate sentiment score for each review

In [30]:
from pyspark.sql.types import FloatType

@udf(returnType = FloatType())
def sentiment_score(col):
  scores = analyser.polarity_scores(col)
  return scores['compound']


review_analysis_df = review_analysis_df.withColumn('sentiment_score', sentiment_score('text'))


#review_analysis_df.select('text', sentiment_score('text').alias('sentiment_score'))['sentiment_score']

display(review_analysis_df)

user_id business_id date review_id text cool funny review_stars useful address categories city is_open latitude longitude name postal_code business_review_count business_stars state average_stars fans user_review_count sentiment_score -3i9bhfvrM3F1wsC9XIB8g pSQFynH1VxkfSmehRXlZWw 2016-11-18 22:03:29 UxxjKGFUJOlTvAXDb-kwIg Fantastic pizza. Small but interesting beer selection. Good, friendly service.
I got the biancoverde pizza, a white pizza with fresh mozzarella, ricotta and a ton of fresh arugula. Delicious. 2 2 5 4 623 E Adams St Sandwiches, Restaurants, Pizza, Salad, Tapas/Small Plates, Italian Phoenix 1 33.44916 -112.065636 Pizzeria Bianco 85004 2276 4.0 AZ 4.07 97 652 0.974 -3i9bhfvrM3F1wsC9XIB8g ghpFh6XpH1TYZhjAGdx-xw 2016-11-18 22:11:54 SQSKmO5D97yIYC0S2RbR_w Really quick for lunch, very tasty pizzas and salads, at a great price.

Staff seems to be a bit reluctant to add "extra" ingredients even if the pizza is meatless. The make your own pizzas are one price. My colleague wanted a simple pizza with extra mushrooms, and the preparer kept adding one or two extra 'shrooms at my friend's urging, and looking back at the manager cautiously. In the meantime, I had a pie with two cheeses, two meats and several different veggies, and nobody batted an eye. 3 2 4 4 3110 N Central Ave Italian, Salad, Food, Pizza, Restaurants Phoenix 1 33.4838 -112.07524 Fired Pie 85012 232 4.0 AZ 4.07 97 652 0.4767 -55DgUo52I3zW9RxkZ-EAQ 3qlqzQrwh8hjBltlgFgsJQ 2015-11-11 04:32:22 NFgnyyp2Kl1nlWIEkXZs4w Great place for late night food. College crowd/seen, usually loud. So that is what to expect. But, with that being said, It is great food & drink. I love go there b/c everyplace else has no late night food. It is one of my go to late night food and drink. Fun place. 0 0 4 0 1011 N 3rd St Restaurants, Mexican Phoenix 0 33.45917 -112.06899 Paz Cantina 85004 264 4.0 AZ 4.59 1 47 0.9562 -55DgUo52I3zW9RxkZ-EAQ 9O-L6F0cMfNmE5i07pN_xQ 2016-08-13 23:40:11 iOTTR1df4vYAtE9WnOHtoA Great cake. Chocolate was perfect, and they are open on Sunday's. Which is really nice for Sunday birthday parties. Def going to come back. Thank you guys for the great cake. 1 0 4 0 15414 N 7th St, Ste 6 Breakfast & Brunch, Food Trucks, Comfort Food, Restaurants, Waffles, Coffee & Tea, Bakeries, Food Phoenix 1 33.626354 -112.06639 Mamma Toledo's The Pie Hole 85022 180 4.0 AZ 4.59 1 47 0.9647 -55DgUo52I3zW9RxkZ-EAQ nn4ZkIZTCd7jJhxs-P9tHA 2016-12-17 16:06:29 zqwxKCkD2PfTRRft5Nv0sg Fun, easy, good 50's Diner. Come here for fun Diner experience. 
If you want fancy brunch with the girls go somewhere else. 
If you have a hang over and had fun last night with the girls and need to share bar stories come here. 0 0 4 0 5220 N 16th St Diners, Breakfast & Brunch, Restaurants, Burgers Phoenix 1 33.51346 -112.047844 5 & Diner 85016 300 3.5 AZ 4.59 1 47 0.9531 -55DgUo52I3zW9RxkZ-EAQ VuYF1vGKLjEFaQfL4Ypwqg 2017-07-29 02:06:31 p1KItC5NgZEvkJksFtUdRQ Sat at the bar. Ordered a whiskey sour with egg whites. You should try it. Perfect with their food. Came out fast and perfect. 0 0 5 0 928 E Pierce St Breakfast & Brunch, Tacos, Cafes, Bars, Restaurants, Nightlife, Mexican Phoenix 1 33.456028 -112.060844 Gallo Blanco 85006 195 4.0 AZ 4.59 1 47 0.8126 -55DgUo52I3zW9RxkZ-EAQ CYWRPE-1IHPBb-zfFO6KRg 2015-11-11 18:27:46 aTeezUJusRSqzrFcUdiuCA Great, rich, European home cooked type meals. Like my Dad makes. Along with awesome cocktails, and decent wine list. Younger business, and local downtown eclectic working professionals (aka gay guys with great taste in food and dress :) ) More dress up a bit dinning, with relaxed atmosphere and good food. Late night food as well !!! Have been back many times. 0 0 5 0 2601 N Central Ave Breakfast & Brunch, Burgers, Mediterranean, Spanish, Modern European, Sandwiches, Comfort Food, Cocktail Bars, American (Traditional), Tapas/Small Plates, Restaurants, Bars, Nightlife Phoenix 0 33.476837 -112.07359 Corduroy 85004 156 4.0 AZ 4.59 1 47 0.9841 -55DgUo52I3zW9RxkZ-EAQ 3awTUGM

#### Create an accuracy column
review_stars :<br>
              1,2 - Negative<br>
                3 - Neutral<br>
              4,5 - positive<br>
              
positive sentiment - compound score >= 0.05<br>
neutral sentiment - compound score (-0.05, +0.05)<br>
negative sentiment - compund score <= -0.05<br>

In [32]:
@udf(returnType = IntegerType())
def accuracy(reviewStars, sentimentScore):
  if (reviewStars < 3 and sentimentScore <= -0.05) or (reviewStars == 3 and sentimentScore > -0.05 and sentimentScore < 0.05) or (reviewStars > 3 and sentimentScore >= 0.05):
    return 1
  else:
    return 0
  
review_analysis_df = review_analysis_df.withColumn('accurate', accuracy('review_stars', 'sentiment_score'))

display(review_analysis_df)

user_id business_id date review_id text cool funny review_stars useful address categories city is_open latitude longitude name postal_code business_review_count business_stars state average_stars fans user_review_count sentiment_score accurate -3i9bhfvrM3F1wsC9XIB8g pSQFynH1VxkfSmehRXlZWw 2016-11-18 22:03:29 UxxjKGFUJOlTvAXDb-kwIg Fantastic pizza. Small but interesting beer selection. Good, friendly service.
I got the biancoverde pizza, a white pizza with fresh mozzarella, ricotta and a ton of fresh arugula. Delicious. 2 2 5 4 623 E Adams St Sandwiches, Restaurants, Pizza, Salad, Tapas/Small Plates, Italian Phoenix 1 33.44916 -112.065636 Pizzeria Bianco 85004 2276 4.0 AZ 4.07 97 652 0.974 1 -3i9bhfvrM3F1wsC9XIB8g ghpFh6XpH1TYZhjAGdx-xw 2016-11-18 22:11:54 SQSKmO5D97yIYC0S2RbR_w Really quick for lunch, very tasty pizzas and salads, at a great price.

Staff seems to be a bit reluctant to add "extra" ingredients even if the pizza is meatless. The make your own pizzas are one price. My colleague wanted a simple pizza with extra mushrooms, and the preparer kept adding one or two extra 'shrooms at my friend's urging, and looking back at the manager cautiously. In the meantime, I had a pie with two cheeses, two meats and several different veggies, and nobody batted an eye. 3 2 4 4 3110 N Central Ave Italian, Salad, Food, Pizza, Restaurants Phoenix 1 33.4838 -112.07524 Fired Pie 85012 232 4.0 AZ 4.07 97 652 0.4767 1 -55DgUo52I3zW9RxkZ-EAQ 3qlqzQrwh8hjBltlgFgsJQ 2015-11-11 04:32:22 NFgnyyp2Kl1nlWIEkXZs4w Great place for late night food. College crowd/seen, usually loud. So that is what to expect. But, with that being said, It is great food & drink. I love go there b/c everyplace else has no late night food. It is one of my go to late night food and drink. Fun place. 0 0 4 0 1011 N 3rd St Restaurants, Mexican Phoenix 0 33.45917 -112.06899 Paz Cantina 85004 264 4.0 AZ 4.59 1 47 0.9562 1 -55DgUo52I3zW9RxkZ-EAQ 9O-L6F0cMfNmE5i07pN_xQ 2016-08-13 23:40:11 iOTTR1df4vYAtE9WnOHtoA Great cake. Chocolate was perfect, and they are open on Sunday's. Which is really nice for Sunday birthday parties. Def going to come back. Thank you guys for the great cake. 1 0 4 0 15414 N 7th St, Ste 6 Breakfast & Brunch, Food Trucks, Comfort Food, Restaurants, Waffles, Coffee & Tea, Bakeries, Food Phoenix 1 33.626354 -112.06639 Mamma Toledo's The Pie Hole 85022 180 4.0 AZ 4.59 1 47 0.9647 1 -55DgUo52I3zW9RxkZ-EAQ nn4ZkIZTCd7jJhxs-P9tHA 2016-12-17 16:06:29 zqwxKCkD2PfTRRft5Nv0sg Fun, easy, good 50's Diner. Come here for fun Diner experience. 
If you want fancy brunch with the girls go somewhere else. 
If you have a hang over and had fun last night with the girls and need to share bar stories come here. 0 0 4 0 5220 N 16th St Diners, Breakfast & Brunch, Restaurants, Burgers Phoenix 1 33.51346 -112.047844 5 & Diner 85016 300 3.5 AZ 4.59 1 47 0.9531 1 -55DgUo52I3zW9RxkZ-EAQ VuYF1vGKLjEFaQfL4Ypwqg 2017-07-29 02:06:31 p1KItC5NgZEvkJksFtUdRQ Sat at the bar. Ordered a whiskey sour with egg whites. You should try it. Perfect with their food. Came out fast and perfect. 0 0 5 0 928 E Pierce St Breakfast & Brunch, Tacos, Cafes, Bars, Restaurants, Nightlife, Mexican Phoenix 1 33.456028 -112.060844 Gallo Blanco 85006 195 4.0 AZ 4.59 1 47 0.8126 1 -55DgUo52I3zW9RxkZ-EAQ CYWRPE-1IHPBb-zfFO6KRg 2015-11-11 18:27:46 aTeezUJusRSqzrFcUdiuCA Great, rich, European home cooked type meals. Like my Dad makes. Along with awesome cocktails, and decent wine list. Younger business, and local downtown eclectic working professionals (aka gay guys with great taste in food and dress :) ) More dress up a bit dinning, with relaxed atmosphere and good food. Late night food as well !!! Have been back many times. 0 0 5 0 2601 N Central Ave Breakfast & Brunch, Burgers, Mediterranean, Spanish, Modern European, Sandwiches, Comfort Food, Cocktail Bars, American (Traditional), Tapas/Small Plates, Restaurants, Bars, Nightlife Phoenix 0 33.476837 -112.07359 Corduroy 85004 156 4.0 AZ 4.59 1 47 0.9841 1 -55DgUo

In [33]:
review_analysis_df.rdd.getNumPartitions()

Out[ 19 ]: 200

In [34]:
review_analysis_df.repartition(30).createOrReplaceTempView('reviewAnalysisVIEW')

In [35]:
spark.catalog.cacheTable('reviewAnalysisVIEW')

In [36]:
# Call .count() to materialize the cache
spark.table("reviewAnalysisVIEW").count()

Out[ 22 ]: 1545286

In [37]:
reviewAnalysisDF = spark.table("reviewAnalysisVIEW")

In [38]:
# Note that the full scan + count in memory takes < 1 second!

reviewAnalysisDF.count()

Out[ 24 ]: 1545286

In [39]:
spark.catalog.isCached("reviewAnalysisVIEW")

Out[ 25 ]: True

In [40]:
display(reviewAnalysisDF.groupby('accurate').count())

accurate count 1 1172360 0 372926

In [41]:
reviewAnalysisDF.write.parquet('/tmp/reviewAnalysisDf')

In [42]:
display(reviewAnalysisDF)

user_id business_id date review_id text cool funny review_stars useful address categories city is_open latitude longitude name postal_code business_review_count business_stars state average_stars fans user_review_count sentiment_score accurate hE1mG_hzS4nlp4_UmHe-eA nkHaix6KenApS8M-liZsCQ 2017-06-02 23:14:54 4s_6QAnXUhrHU8hjl39rsg Best pizza in town. 
Yes, I said it. Better than the famous Pizzeria Bianco. 

I have been eating at Christopher's since 2005 I believe (at their old and better location) I'd say I was there 25+ times. Never had any issues with the service. 
Plus: where else will you get such a soufflé? 0 0 5 0 2502 E Camelback Rd, Ste 102 Lounges, French, American (New), Restaurants, Bars, Nightlife Phoenix 0 33.511417 -112.02855 Christopher's and Crush Lounge 85016 306 4.0 AZ 4.32 1 95 0.9136 1 NMI-8KI3WLuQ3E4xW0s2Xw oxv2UyI5yF6yawPU20tOxA 2016-09-03 06:03:32 ioFc-bzjlrW6WQnY5B1Gmg This place was good. 
Their queso fundito was tasty and the homemade tortillas were great.
Good service and the setting is great. 
Can't wait to return when it's cooler so we can enjoy the cute patio seating. 
: ) 0 0 4 1 6910 E Main St Restaurants, Bars, Tex-Mex, Beer Bar, Mexican, Nightlife Scottsdale 1 33.493332 -111.932106 Old Town Tortilla Factory 85251 440 3.0 AZ 4.07 0 44 0.966 1 E8YUkyDranomGC0Ww6tF1g 8v7V-gBgUf_J9ZmJDnvC2Q 2018-10-11 09:42:51 XW_gShwF9Gk2B7kUvtKQgw This place is great, however the last time I came to get food they took abnormally long to get the food out. It took 40 minutes for me to get my 12 piece BONELESS wings with fries. I would understand a little more if the wings were bone in, but even that is still not a good excuse for a 40 minute wait time. The restaurant was moderately full but it was not packed with people. So I could understand an extra 5 minute wait on top of the 15 minute average. This is also not the only time I was stuck waiting around 40 minutes, this has happened 3 other times all consecutively. Other than that the food itself is good, I just wish they would be faster with getting their food out. 0 0 2 0 8024 N 51st Ave American (Traditional), Chicken Wings, Restaurants Glendale 1 33.554 -112.1693 ATL Wings 85302 178 4.0 AZ 3.5 0 2 -0.1904 1 R0KVWeN9xR-F6j4z5k9wXQ NJ0RzuWd5xDqfJejYQZ65g 2006-07-11 23:02:13 gQA90bgLe6tpVCcNS8wN0A Although I am not sure it is worth the hour wait, I loved the concept. The burger was delicious, but the sweet potato fries were my favorite part. The fries come in cute little mini shopping carts and I recommend going half and half w/ regular fries for the variety. Yes, it is very trendy but we had a great time! We split a salad and a burger so it is not too pricey if you go that way. Also, they have a great variety of cocktails which left me very happy by the time we left. 2 0 4 1 3146 E Camelback Rd Nightlife, Bars, American (Traditional), Beer, Wine & Spirits, Burgers, Food, Fast Food, Restaurants, Sushi Bars Phoenix 1 33.511223 -112.01391 Delux 85016 998 4.0 AZ 3.64 63 439 0.9921 1 Al2g2P9gt057Julh1qTPtQ ELUUibdDcrZHyvE-e-QsVw 2014-11-01 22:21:43 Pn4_csggXiJ1eAMCm59Z_A First time here, couldn't decide so I got the ultimate grilled cheese and the hubby got the California grilled chicken sandwich, both were ah-mazing!! can't wait to come back! 0 0 5 1 6430 S McClintock Dr American (Traditional), Breakfast & Brunch, Restaurants Tempe 1 33.362507 -111.91275 Mac's Broiler & Tap 85283 214 3.5 AZ 5.0 0 10 0.0 0 -inp099-1gsJF3KPaS-mbg szhJLmdLDVFTevm8fu0T4A 2016-07-06 04:02:16 wF9ZeC68SXnzVzToRi22Ew Great Wall is good. The food is good especially if you know what you are receiving from
the carts that pass by. I enjoyed it. For people
complaining about the restaurant being crowded/loud it's typical of a Dim Sum restaurant. Especially since usually those attending the restaurant are doing so for family reunions or special occasions. 0 0 4 0 3446 W Camelback Rd, Ste 155 Cantonese, Dim Sum, Chinese, Restaurants Phoenix 1 33.510986 -112.13328 Great Wall Cuisine 85017 465 3.5 

In [43]:
display(reviewAnalysisDF.select('review_stars').distinct())

review_stars 1 3 5 4 2

In [44]:
%fs ls tmp/reviewAnalysisDf

path name size dbfs:/tmp/reviewAnalysisDf/_SUCCESS _SUCCESS 0 dbfs:/tmp/reviewAnalysisDf/_committed_4055190317912707360 _committed_4055190317912707360 3054 dbfs:/tmp/reviewAnalysisDf/_started_4055190317912707360 _started_4055190317912707360 0 dbfs:/tmp/reviewAnalysisDf/part-00000-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2620-1-c000.snappy.parquet part-00000-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2620-1-c000.snappy.parquet 22496983 dbfs:/tmp/reviewAnalysisDf/part-00001-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2621-1-c000.snappy.parquet part-00001-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2621-1-c000.snappy.parquet 22437324 dbfs:/tmp/reviewAnalysisDf/part-00002-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2622-1-c000.snappy.parquet part-00002-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2622-1-c000.snappy.parquet 22445475 dbfs:/tmp/reviewAnalysisDf/part-00003-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2623-1-c000.snappy.parquet part-00003-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2623-1-c000.snappy.parquet 22476154 dbfs:/tmp/reviewAnalysisDf/part-00004-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2624-1-c000.snappy.parquet part-00004-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2624-1-c000.snappy.parquet 22434041 dbfs:/tmp/reviewAnalysisDf/part-00005-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2625-1-c000.snappy.parquet part-00005-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2625-1-c000.snappy.parquet 22425221 dbfs:/tmp/reviewAnalysisDf/part-00006-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2626-1-c000.snappy.parquet part-00006-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2626-1-c000.snappy.parquet 22389287 dbfs:/tmp/reviewAnalysisDf/part-00007-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2627-1-c000.snappy.parquet part-00007-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2627-1-c000.snappy.parquet 22442085 dbfs:/tmp/reviewAnalysisDf/part-00008-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2628-1-c000.snappy.parquet part-00008-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2628-1-c000.snappy.parquet 22533750 dbfs:/tmp/reviewAnalysisDf/part-00009-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2629-1-c000.snappy.parquet part-00009-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2629-1-c000.snappy.parquet 22551580 dbfs:/tmp/reviewAnalysisDf/part-00010-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2630-1-c000.snappy.parquet part-00010-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2630-1-c000.snappy.parquet 22436227 dbfs:/tmp/reviewAnalysisDf/part-00011-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2631-1-c000.snappy.parquet part-00011-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2631-1-c000.snappy.parquet 22404201 dbfs:/tmp/reviewAnalysisDf/part-00012-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2632-1-c000.snappy.parquet part-00012-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2632-1-c000.snappy.parquet 22561309 dbfs:/tmp/reviewAnalysisDf/part-00013-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2633-1-c000.snappy.parquet part-00013-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2633-1-c000.snappy.parquet 22443180 dbfs:/tmp/reviewAnalysisDf/part-00014-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2634-1-c000.snappy.parquet part-00014-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2634-1-c000.snappy.parquet 22400934 dbfs:/tmp/reviewAnalysisDf/part-00015-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2635-1-c000.snappy.parquet part-00015-tid-4055190317912707360-9c30935f-421c-4172-9507-d8282ffc1d44-2635-1-c000.snappy.parquet 22516772 dbfs:/tmp/rev

### 3: Vector Assembly
Once we are through with the encoder creation step, it is time to essemble the encoders and all the input and output columns to form a final vector_generator that will be passed as input to the machine learning pipeline.

In [46]:
import pyspark.ml.feature as ft

featuresCreator = ft.VectorAssembler(inputCols=['cool', 'funny', 'useful', 'is_open', 'business_review_count', 'business_stars', 'average_stars', 'fans', 'user_review_count', 'sentiment_score'],outputCol='features')


### 4: Estimator Creation
This is the step where we select the machine learning model that we wish to utilize. Here, we create an Estimator object that contains the machine learning model along with all the hyper optimization parameters that need to be passed to it. Here, we are using LogisticRegression.

In [48]:
import pyspark.ml.classification as cl


logistic_regression_model = cl.LogisticRegression(maxIter=10,regParam=0.01,labelCol='review_stars', family = 'multinomial')
print(type(logistic_regression_model))



<class 'pyspark.ml.classification.LogisticRegression'>

### 5: Pipeline Creation

In [50]:
from pyspark.ml import Pipeline


pipeline = Pipeline(stages=[featuresCreator,logistic_regression_model])
print(type(pipeline))

<class 'pyspark.ml.pipeline.Pipeline'>

### 6: Dataset Splitting

In [52]:
train, test = reviewAnalysisDF.randomSplit([0.7, 0.3], seed=666)

### 7: Model Fitting

In [54]:
# This creates a model by training on the births_train dataset using the Pipeline we created
model = pipeline.fit(train)
print(type(model))

# This step uses the model that we created in the previous step to generate the output column for births_test dataset
test_model = model.transform(test)
print(type(test_model))

<class 'pyspark.ml.pipeline.PipelineModel'>
<class 'pyspark.sql.dataframe.DataFrame'>

In [55]:
display(test_model.select('prediction').distinct())

prediction 1.0 4.0 3.0 5.0

We observe that our model does not give any 2 star ratings. Let's check how accurate it is.

### 8: Performance Evaluation

In [58]:
import pyspark.ml.evaluation as ev


# Create an object of the Evaluator class that evaluates our model based on the rawPredictionCol and the label that we need to predict
evaluator = ev.MulticlassClassificationEvaluator(predictionCol='prediction',labelCol='review_stars')

# Extract the needed evaluation criteria from the object
print(evaluator.evaluate(test_model,{evaluator.metricName: 'accuracy'}))
# print(evaluator.evaluate(test_model,{evaluator.metricName: 'areaUnderPR'}))

0.510918028053072

We observe an accuracy of 51 percent on this baseline model

In [60]:
%fs ls reviewAnalysisDf.tsv

path name size dbfs:/reviewAnalysisDf.tsv/_SUCCESS _SUCCESS 0 dbfs:/reviewAnalysisDf.tsv/_committed_1137497451089006343 _committed_1137497451089006343 114 dbfs:/reviewAnalysisDf.tsv/_started_1137497451089006343 _started_1137497451089006343 0 dbfs:/reviewAnalysisDf.tsv/part-00000-tid-1137497451089006343-6e19e93f-ef33-4939-a015-adc23d0f3dcf-4098-1-c000.csv part-00000-tid-1137497451089006343-6e19e93f-ef33-4939-a015-adc23d0f3dcf-4098-1-c000.csv 1248225473